In [1]:
import itertools
import numpy as np
import os
import seaborn as sns
from tqdm import tqdm
from dataclasses import asdict, dataclass, field
import vsketch
import shapely.geometry as sg
from shapely.geometry import box, MultiLineString, Point, MultiPoint, Polygon, MultiPolygon, LineString
import shapely.affinity as sa
import shapely.ops as so
import matplotlib.pyplot as plt
import pandas as pd

import vpype_cli
from typing import List, Generic
from genpen import genpen as gp, utils as utils
from scipy import stats as ss
import geopandas
from shapely.errors import TopologicalError
import functools
%load_ext autoreload
%autoreload 2
import vpype
from skimage import io
from pathlib import Path
import fn
import bezier

from sklearn.preprocessing import minmax_scale
from skimage import feature
from genpen.utils import Paper
from genpen.genpen import *
from genpen import subdivide as sd
from functools import partial
from genpen.grower import Grower, GrowerParams

In [65]:
image_path= '/home/naka/art/wigglesphere.jpg'

paper_size:str = '7x5 inches'
border:float=15  # mm
image_rescale_factor:float=0.04
smooth_disk_size:int=1
hist_clip_limit=0.1
hist_nbins=32
intensity_min=0.
intensity_max=1.
hatch_spacing_min=0.35  # mm
hatch_spacing_max=1.1 # mm
pixel_width=1 # mm
pixel_height=1 # mm
angle_jitter='ss.norm(loc=10, scale=0).rvs'  # degrees
pixel_rotation='0'  # degrees
merge_tolerances=[0.3, 0.4,]  # mm
simplify_tolerances=[0.2,]  # mm
savedir='/home/naka/art/plotter_svgs'

In [66]:
# make page
paper = Paper(paper_size)
drawbox = paper.get_drawbox(border)


In [67]:
bps = gp.circle_pack_within_poly(drawbox, rads=[20, 10, 5, 2.5])

 75%|███████▌  | 3/4 [00:00<00:00, 12.10it/s]

In [68]:
bps2 = gp.circle_pack_within_poly(drawbox, rads=[20, 10, 5, 2.5])


 75%|███████▌  | 3/4 [00:00<00:00, 12.93it/s]

In [69]:
bps = bps.difference(bps2.boundary.buffer(0.1))

In [70]:
bps = so.unary_union([bps2.difference(bps), bps.buffer(-0.1)])

In [71]:
n_layers = 1

In [72]:
layers = []
for ii in range(n_layers):
    fills = []
    for p in bps:
        xjitter_func = 0
        yjitter_func = ss.norm(loc=0, scale=np.random.uniform(0.1, 1.5)).rvs
        dist_from_center = p.centroid.distance(bps.centroid)
        a = np.interp(dist_from_center, [0, 150], [0, 1020])
        bhf = gp.BezierHatchFill(
            spacing=np.random.uniform(0.2, 0.4),
            degrees=a,
            poly_to_fill=p, 
            xjitter_func=xjitter_func, 
            yjitter_func=yjitter_func,
            fill_inscribe_buffer=1.4,
            n_nodes_per_line=15,
            n_eval_points=100,
        )
        fills.append(bhf.p)

    fills = [f for f in fills if f.length > 0]
    layer = gp.merge_LineStrings(fills)
    layers.append(layer)

 75%|███████▌  | 3/4 [00:10<00:03,  3.47s/it]


In [111]:
sk = vsketch.Vsketch()
sk.size(paper.page_format_mm)
sk.scale('1mm')
sk.penWidth('0.3mm')
for i, layer in enumerate(layers):
    sk.stroke(i+1)
    sk.geometry(layer)

# sk.stroke(len(layers)+2)
# sk.geometry(blss)
    
sk.display(color_mode='layer')

<?xml version="1.0" encoding="utf-8" ?>
 
 
 
 
 image/svg+xml 
 
 2021-09-22T22:44:29.518934 
 
 
 
 
 
 
 <polyline points="358.7858,70.7438 358.6728,70.8668 358.4754,71.081 358.2779,71.295 358.0805,71.5092 357.8835,71.7238 357.6871,71.9388 357.4915,72.1544 357.2967,72.3708 357.103,72.5881 356.9103,72.8064 356.7189,73.0256 356.5286,73.2459 356.3396,73.4672 356.1518,73.6895 355.9651,73.9128 355.7796,74.1371 355.5951,74.3623 355.4117,74.5884 355.2291,74.8152 355.0474,75.0427 354.8663,75.2708 354.6858,75.4995 354.5059,75.7285 354.3263,75.9578 354.1469,76.1874 353.9676,76.417 353.7883,76.6466 353.6088,76.8761 353.4289,77.1052 353.2484,77.3337 353.1051,77.5137"/>
 <polyline points="351.4009,77.4356 351.4823,77.3571 351.6888,77.1507 351.8917,76.9412 352.0911,76.7288 352.2874,76.5137 352.4806,76.2959 352.6709,76.0757 352.8585,75.8532 353.0435,75.6285 353.2262,75.4017 353.4065,75.173 353.5847,74.9425 353.7611,74.7103 353.9357,74.4768 354.1088,74.2419 354.2808,74.006 354.4517,73.7692 354.6219,73.5319 354.7918,73.2942 354.9615,73.0564 355.1314,72.8188 355.3018,72.5816 355.4731,72.3451 355.6454,72.1096 355.819,71.8751 355.9942,71.642 356.1712,71.4105 356.3502,71.1806 356.5313,70.9525 356.7145,70.7263 356.9,70.5019 357.0877,70.2795 357.2775,70.0589 357.4694,69.84 357.6632,69.6228 357.8587,69.407 358.0556,69.1923 358.2535,68.9786 358.4522,68.7656 358.4993,68.7153"/>
 <polyline points="357.9574,67.1917 357.9552,67.1937 357.7356,67.3889 357.5166,67.5846 357.2988,67.7814 357.0827,67.9796 356.8688,68.1796 356.6574,68.3818 356.4488,68.5865 356.2434,68.7938 356.0413,69.004 355.8425,69.217 355.6472,69.4329 355.4553,69.6517 355.2666,69.8733 355.081,70.0976 354.8984,70.3243 354.7183,70.5533 354.5406,70.7842 354.3648,71.0168 354.1906,71.2508 354.0175,71.4857 353.8452,71.7213 353.6732,71.9571 353.501,72.1928 353.3284,72.4281 353.1549,72.6627 352.9801,72.8961 352.8037,73.1282 352.6254,73.3586 352.4449,73.5872 352.2619,73.8137 352.0765,74.0381 351.8882,74.2601 351.6972,74.4796 351.5032,74.6967 351.3064,74.9114 351.1066,75.1235 350.9039,75.3331 350.6983,75.5403 350.4898,75.745 350.2784,75.9472 350.0642,76.1471 349.8471,76.3444 349.627,76.5392 349.4038,76.7314 349.1774,76.9207 348.9474,77.1071 348.7136,77.2902 348.4756,77.4698 348.233,77.6453 348.0952,77.7406"/>
 <polyline points="349.534,74.9465 349.5441,74.938 349.7689,74.7473 349.9922,74.5551 350.2134,74.3613 350.4321,74.1653 350.6479,73.9668 350.8603,73.7655 351.0691,73.5611 351.2739,73.3533 351.4747,73.142 351.6713,72.9271 351.8636,72.7086 352.0518,72.4866 352.2361,72.2613 352.4167,72.0327 352.5938,71.8013 352.768,71.5673 352.9396,71.3311 353.1091,71.0932 353.2771,70.8539 353.4441,70.6139 353.6108,70.3735 353.7776,70.1332 353.9452,69.8936 354.114,69.655 354.2846,69.418 354.4574,69.1828 354.6328,68.9499 354.8112,68.7195 354.9928,68.4919 355.1779,68.2672 355.3665,68.0455 355.5586,67.8269 355.7543,67.6113 355.9535,67.3986 356.1558,67.1887 356.3612,66.9813 356.5691,66.7761 356.7793,66.5729 356.9913,66.3711 357.2045,66.1705 357.3343,66.049"/>
 <polyline points="356.4652,64.9231 356.3388,65.0491 356.1304,65.2539 355.9211,65.4579 355.7114,65.6616 355.502,65.8656 355.2935,66.0702 355.0862,66.276 354.8808,66.4833 354.6777,66.6926 354.4773,66.9041 354.2797,67.1182 354.0854,67.335 353.8944,67.5546 353.7068,67.7771 353.5227,68.0026 353.3419,68.231 353.1643,68.462 352.9897,68.6956 352.8178,68.9315 352.6482,69.1694 352.4805,69.409 352.3143,69.6497 352.149,69.8913 351.9843,70.1333 351.8194,70.3753 351.654,70.6167 351.4875,70.8573 351.3194,71.0964 351.1493,71.3339 350.9768,71.5693 350.8015,71.8024 350.6233,72.0328 350.4417,72.2605 350.2569,72.4854 350.1573,72.6028"/>
 <polyline points="350.2354,70.3424 350.3092,70.2344 350.472,69.9907 350.633,69.7455 350.7926,69.4991 350.9512,69.2518 351.1092,69.0041 351.2672,68.7562 351.4256,68.5088 351.5848,68.2621 351.7454,68.0165 351.9077,67.7724 352.0721,67.5301 352.2391,67.2899 352.4088,67.0522 352.5816,66.817 352.7576,66.5846 352.9371,66.3551 353.1199,66.1285 353.3063,65.9

In [112]:
sk = vsketch.Vsketch()
sk.size(paper.page_format_mm)
sk.scale('1mm')
sk.penWidth('0.08mm')
for i, layer in enumerate(layers):
    sk.stroke(i+1)
    sk.geometry(layer)

for tolerance in [0.05, 0.1, 0.2,  0.3, 0.5, 0.7]:
    sk.vpype(f'linemerge --tolerance {tolerance}mm')
sk.vpype('linesimplify --tolerance 0.1 linesort')

sk.display(color_mode='layer')

<?xml version="1.0" encoding="utf-8" ?>
 
 
 
 
 image/svg+xml 
 
 2021-09-22T22:44:48.593723 
 
 
 
 
 
 
 
 <polyline points="367.8694,72.7496 368.6242,72.6383 368.2186,72.4685 369.2835,72.1955 368.7032,71.2214 371.8584,65.0456 373.5661,63.9635 370.2288,70.4543 371.1141,70.146 373.3703,65.2151 374.2381,63.5608 374.5089,63.3985 372.094,68.5487 371.4948,70.0506 371.6881,70.7815 371.3259,71.266 373.0656,70.5295 373.0922,70.9076 373.3165,70.8949 373.4651,70.5092 374.0044,70.4833 373.9698,70.8628 375.1819,69.8026 377.1573,65.1184 379.1518,61.3862 376.9879,65.0673 374.9145,69.7712 374.0388,69.7282 375.583,65.8829 377.5416,61.849 379.1518,61.3862 379.3434,61.0665 379.1518,61.3862 381.4369,60.3174 379.438,63.3276 377.6749,66.5142 376.0825,69.9457 376.5443,70.0614 378.1582,66.6601 379.9545,63.4835 382.3542,60.0062 382.9213,59.8641 379.9284,64.7152 377.3902,70.3194 377.1495,71.4375 377.373,71.1161 378.0658,71.834 378.2614,71.5085 378.4098,72.0139 378.2607,71.5081 378.664,70.8627 380.4823,66.1219 382.0383,62.8728 383.9573,59.6046 385.182,59.2979 383.4493,62.059 382.3226,64.1981 380.886,67.4834 379.5247,71.3603 378.8628,72.2855 379.2818,72.1009 379.5114,72.2711 379.1217,72.4526 380.9927,74.159 381.8119,73.3745 384.0302,67.1927 386.6805,61.7946 388.6258,58.7282 389.8429,58.5926 388.3489,61.0586 386.69,64.2767 384.8348,68.6751 382.7458,74.6992 382.3059,75.4355 381.9234,75.5326 381.7589,76.0356 379.0902,75.6047 377.0774,75.6 376.6799,75.6632 376.1521,76.5858 377.593,75.8903 378.5911,75.6058 380.8278,75.4545 381.4542,75.4849 381.5505,75.6455 378.3586,75.1928 376.7138,75.3952 376.1925,75.9481 375.8809,76.7289 374.2747,77.4075 372.7385,77.768 373.3189,77.4534 372.8182,78.4048 373.9952,78.3191 373.8344,77.1319 371.7327,77.2764 370.8566,78.0296 368.5006,78.3884 366.9692,78.9368 366.3378,79.4277 365.9174,80.0373 365.4802,81.6558 364.712,81.6483 364.672,81.3787 365.0577,81.4033 365.0129,81.1013 364.6228,81.0473 364.9477,80.3399 364.5623,80.1968 364.9433,80.2508 364.9379,79.7237 364.5645,79.6214 364.9433,79.6134 365.4765,79.2249 366.7646,78.8216 370.2994,78.4946 368.6783,79.899 368.1953,80.7555 368.1034,82.1144 368.6944,84.6759 369.2251,83.0808 368.874,81.1377 368.9753,80.3484 369.2614,79.6631 369.6102,79.1768 371.1438,78.4692 370.2994,78.4946 370.8566,78.0296 372.7385,77.768 371.1438,78.4692 372.8182,78.4048 372.2932,79.1115 370.9582,79.7721 370.0049,80.6459 369.5657,81.5271 369.2251,83.0808 370.2399,85.8894 371.2483,84.4089 371.6505,86.9326 371.6022,87.4615 371.3044,87.5841 370.4882,87.8754 369.0678,87.9796 370.9347,88.0563 370.2399,85.8894 369.8926,86.5072 369.6788,87.2332 369.8103,87.5433 371.5811,87.5707 372.7176,86.687 373.0962,86.0539 373.2992,85.3218 373.7916,81.5036 372.4274,82.8561 371.2483,84.4089 370.8846,82.2696 371.1633,80.7339 372.2932,79.1115 374.0075,78.4253 373.9952,78.3191 375.4723,78.1209 375.8271,76.9189 376.0711,76.891 375.9838,77.335 374.0075,78.4253 374.0353,79.9422 374.8774,79.1574 375.4723,78.1209 375.847,78.0499 375.4466,79.4778 374.6088,80.6989 373.7916,81.5036 374.0353,79.9422 371.8562,81.4061 370.5626,82.6526 368.0193,86.2297 367.8436,85.9178 368.6944,84.6759 369.2903,87.2317 368.127,86.8374 367.7522,87.0078 367.305,86.8119 367.0735,87.1609 366.6281,85.8563 366.399,86.1819 365.9315,86.186 365.6725,91.5444 365.9717,94.3333 366.871,97.0713 369.0052,101.6054 369.372,99.8067 367.9534,96.5104 367.2753,93.7537 367.1856,91.416 367.46,88.5421"/>
 <polyline points="370.0029,90.6456 370.2803,89.4278 369.9435,89.2901 369.7754,90.0099 369.5092,89.0847 368.7771,89.559 368.617,90.1379 368.8704,89.7563 368.0781,89.8491 367.9549,92.7579 368.1981,94.6135 368.7468,96.4431 369.5423,98.2425 370.2682,98.8702 368.6963,94.5712 368.4118,92.7191 368.4048,90.6669 368.7835,91.7252 368.7766,93.1572 368.9854,94.5466 369.5569,96.2309 370.0423,93.7352 369.8269,94.8583 370.9966,95.0168 371.9542,89.9281 373.3284,90.1046 371.3776,99.3222 370.1692,107.6346 369.7525,114.9464 370.006,121.9387 368.9957,122.4799 369.8851,123.0891 370.0602,124.1929 370.7105

In [75]:
def vsketch_to_shapely(sketch):
    return [[LineString([Point(pt.real, pt.imag) for pt in lc]) for lc in layer] for layer in sketch.document.layers.values()]

In [76]:
layer = sk.document.layers[1]

In [77]:
mls = gp.make_like(MultiLineString([LineString([Point(pt.real, pt.imag) for pt in lc]) for lc in layer]), drawbox)

In [97]:
ds = [150 - ls.distance(drawbox.centroid) for ls in mls]

In [98]:
ds = np.array(ds) ** 0.5
ds = ds/ ds.sum()

In [109]:
frac_keep = 0.95
n_keep = int(frac_keep * len(mls))
pmls = MultiLineString(list(np.random.choice(mls, size=n_keep, replace=False, p=ds)))
rlayers = [pmls]

<ipython-input-109-ea0547e9afe3>:3: FutureWarning: The input object of type 'LineString' is an array-like implementing one of the corresponding protocols (`__array__`, `__array_interface__` or `__array_struct__`); but not a sequence (or 0-D). In the future, this object will be coerced as if it was first converted using `np.array(obj)`. To retain the old behaviour, you have to either modify the type 'LineString', or assign to an empty array created with `np.empty(correct_shape, dtype=object)`.
  pmls = MultiLineString(list(np.random.choice(mls, size=n_keep, replace=False, p=ds)))
<ipython-input-109-ea0547e9afe3>:3: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  pmls = MultiLineString(list(np.random.choice(mls, size=n_keep, replace=False, p=ds)))


In [110]:
sk = vsketch.Vsketch()
sk.size(paper.page_format_mm)
sk.scale('1mm')
sk.penWidth('0.08mm')
for i, layer in enumerate(rlayers):
    sk.stroke(i+1)
    sk.geometry(layer)

for tolerance in [0.05, 0.1, 0.2,  0.3, 0.5, 0.7]:
    sk.vpype(f'linemerge --tolerance {tolerance}mm')
    sk.vpype('linesimplify --tolerance 0.1 linesort')

sk.display(color_mode='layer')

<?xml version="1.0" encoding="utf-8" ?>
 
 
 
 
 image/svg+xml 
 
 2021-09-22T22:44:13.700594 
 
 
 
 
 
 
 <polyline points="214.0584,417.5803 207.5571,417.6256 201.9955,416.5475 198.9482,416.267 198.3262,414.8024 201.5174,414.7018 203.7931,414.8819 207.8062,415.6682 211.9129,416.2562 214.5213,416.9437 214.8256,416.436 212.8123,415.7795 208.1291,414.9839 203.1365,413.4144 201.1845,413.2631 197.9905,413.4176 197.8691,412.0766 202.613,413.0946 207.3052,414.5858 213.1506,415.0625 215.1876,415.7215 215.4414,415.1028 213.8393,414.3177 208.4239,413.6442 203.2323,411.7819 199.4694,411.2478 199.8026,411.0481 203.1197,411.3059 208.1115,412.1622 211.5366,412.0609 213.618,412.6149 214.3552,412.1497 213.6353,410.0053 212.9395,405.1761 212.697,404.9563 213.5885,411.7156 212.4974,411.8715 212.9534,411.7389 212.7068,411.556 212.2039,411.6451 212.5182,411.4161 212.048,411.5038 211.5296,411.0262 212.1764,410.5996 211.7578,408.6273 211.1162,406.7547 210.7232,406.2155 210.2716,405.9987 209.7584,406.1195 209.1046,406.718 209.155,406.9193 209.4596,406.5791 209.1629,406.951 209.2634,407.2854 209.5341,406.8768 209.7398,407.4946 209.4993,407.9447 210.0742,408.2903 209.7985,408.5917 210.1127,408.3717 209.8464,408.6928 210.0213,409.0162 210.3138,408.7686 210.4551,408.2113 211.4326,410.3561 211.0613,410.5095 210.5331,411.0527 208.7262,410.8593 204.4556,409.904 201.185,409.9558 200.8304,409.2567 199.587,409.8088 199.2922,409.5568 198.2296,409.4327 197.5841,410.6813 195.7078,411.3032 194.3207,411.4277 193.1607,411.0712 192.2303,410.2282 190.1383,406.3128 189.4893,407.0633 188.8832,407.1258 188.3431,406.7943 187.9913,405.5868 187.8361,401.8215 187.3498,405.9963 187.353,407.8211 186.3515,407.7364 187.0124,407.9965 186.475,407.9067 185.4424,413.1024 184.1994,413.7436 185.2463,408.9875 185.45,407.7033 185.3205,407.4873 183.5963,413.9594 183.2487,414.0708 185.1179,407.1045 186.5682,406.6271 186.8014,403.6332 186.7147,402.0153 185.8,399.1413 185.3189,399.3635"/>
 
 <polyline points="189.7867,404.8916 189.2783,403.8858 189.1921,402.0896 187.9127,399.8205 187.8361,401.8215 186.7353,398.5636 189.3867,397.2581 190.9215,396.8206 192.1412,397.0507 193.0312,397.9794 193.5216,399.051 194.8528,403.2658 195.4071,404.202 196.1169,404.8087 196.9975,405.0537 198.4195,404.8553 202.163,403.1744 198.7681,404.1169 197.5012,403.9868 196.7376,403.4939 196.1393,402.6509 195.5603,401.0635 195.4257,400.5258 195.7952,399.9392 195.0463,398.7718 194.523,398.2482 194.9103,398.523 195.7952,399.9392 194.523,398.2482 194.059,398.1326 194.523,398.2482 193.8257,397.6725 194.3892,397.4271 194.9627,397.4592 196.6187,398.6705 197.2415,398.8533 196.6677,398.4589 195.4781,396.905 194.9853,396.5246 194.2161,396.5015 193.494,396.8965 192.5795,394.6481 191.9395,394.6642 190.7832,395.0032 186.3497,397.2748 184.8598,397.2824 184.8801,398.4066 184.7414,398.7328 184.3036,397.0193 184.4979,399.4134 184.1518,396.954 182.5779,396.4759 182.4506,398.4667 183.225,403.9767 183.2096,406.6597 182.5442,409.5739 180.6859,414.4287 181.8266,410.7644 182.2432,408.1088 182.1294,402.4486 182.4506,398.4667 181.9176,396.3706 182.0612,397.1097 182.7252,398.2733 182.9624,399.3601 183.3677,406.4954 183.0658,410.3652 181.9836,414.3343 183.003,412.1443 182.6306,414.1456 183.8461,410.443 184.1885,408.3091 184.0278,406.1666 183.003,412.1443 184.9181,406.6819 185.0015,406.8583 184.4453,409.3408 182.6728,414.215 180.9673,414.4198 183.8294,405.4523 184.0278,406.1666 184.252,404.6673 184.1744,404.2627 183.8294,405.4523 182.4704,401.8843 182.9644,405.5811 182.7478,408.4733 182.1941,410.5921 180.6832,414.1755 180.5652,414.4228 179.9344,414.3918 180.3748,412.718 180.6446,410.6595 180.2676,405.0129 179.0439,406.3986 178.6338,404.9421 176.7423,404.7573 171.691,404.7628 171.7453,404.2001 178.9232,403.9439 178.9902,403.2387 178.4989,403.1855 175.6268,403.0735 171.915,403.2723 175.0514,403.052 178.9957,402.4059 176.1593,402.3288 172.0415,402.7675 172.1286,402.5108 178.9727,401.9394 178.9327,401.6523 175.3092,401.7486 172.6362,401.2853 171

In [113]:
plot_id = fn.new_plot_id()

saved 20210922-224529_191352-4e22b-c23cd2 to s3://algorithmic-ink/current_plot_id


In [114]:
savedir='/home/naka/art/plotter_svgs'

In [115]:
savepath = Path(savedir).joinpath(f'{plot_id}.svg').as_posix()
sk.save(savepath)

In [116]:
sk.vpype('stat')

========= Stats ========= 
Current page size: (672.0, 480.00000000000006)
Layer 1
  Length: 188854.83071660917
  Pen-up length: 12963.50949606442
  Total length: 201818.3402126736
  Mean pen-up length: 9.12280752713893
  Median pen-up length: 5.426022280206396
  Path count: 1422
  Segment count: 66939
  Mean segment length: 2.8212974606224948
  Bounds: (56.853098413739886, 57.38364869841492, 615.2551999297791, 422.12301295846316)
Totals
  Layer count: 1
  Length: 188854.83071660917
  Pen-up length: 12963.50949606442
  Total length: 201818.3402126736
  Path count: 1422
  Segment count: 66939
  Mean segment length: 2.8212974606224948
  Bounds: (56.853098413739886, 57.38364869841492, 615.2551999297791, 422.12301295846316)


In [337]:
pmls.length

260761.31700853925